In [1]:
#|default_exp app

# Initialization

## Get/Set Environment Variables

If you want to run this locally without having to set up the environment variables in your system, you can create a file called `tts_openai_secrets.py` in the root directory with this content:
```python
import os
os.environ['OPENAI_API_KEY'] = 'sk-XXXXXXXXXXXXXXXXXXXXXX'
os.environ['CARTESIA_API_KEY'] = 'XXXXXXXXXXXXXXXXXXXXXX'
os.environ["ALLOWED_OAUTH_PROFILE_USERNAMES"]= '<huggingface-username1>,<huggingface-username2>'
```

In [2]:
#| export

import os
secret_import_failed = False
try:
    # don't need the openai api key in a variable
    _ = os.environ['OPENAI_API_KEY']
    print('OPENAI_API_KEY environment variable was found.')
except:
    print('OPENAI_API_KEY environment variable was not found.')
    secret_import_failed = True
try:
    CARTESIA_API_KEY = os.environ['CARTESIA_API_KEY']
    print('CARTESIA_API_KEY environment variable was found.')
except:
    print('CARTESIA_API_KEY environment variable was not found.')
    secret_import_failed = True
try:
    temp_ALLOWED_OAUTH_PROFILE_USERNAMES = os.environ['ALLOWED_OAUTH_PROFILE_USERNAMES']
    ALLOWED_OAUTH_PROFILE_USERNAMES = tuple([o for o in temp_ALLOWED_OAUTH_PROFILE_USERNAMES.split(',') if o not in ('','None')])
    del temp_ALLOWED_OAUTH_PROFILE_USERNAMES
    print(f'ALLOWED_OAUTH_PROFILE_USERNAMES environment variable was found. {ALLOWED_OAUTH_PROFILE_USERNAMES}')
except:
    print('ALLOWED_OAUTH_PROFILE_USERNAMES environment variable was not found.')
    secret_import_failed = True

if secret_import_failed == True:
    import tts_openai_secrets
    _ = os.environ['OPENAI_API_KEY']
    CARTESIA_API_KEY = os.environ['CARTESIA_API_KEY']
    ALLOWED_OAUTH_PROFILE_USERNAMES = os.environ['ALLOWED_OAUTH_PROFILE_USERNAMES']
    print('import tts_openai_secrets succeeded')

OPENAI_API_KEY environment variable was not found.
CARTESIA_API_KEY environment variable was not found.
ALLOWED_OAUTH_PROFILE_USERNAMES environment variable was not found.
import tts_openai_secrets succeeded


In [3]:
#| export
# If REQUIRE_AUTH environemnt variable is set to 'false' (from secrets) and HF_SPACE != 1 then we
# are running locally and don't require authentication and authorization, otherwise we do.
# We are using paid API's so don't want anybody/everybody to be able to use our paid services.
if os.environ.get("REQUIRE_AUTH",'true') == 'false' and os.environ.get('HF_SPACE',0) != 1:
    REQUIRE_AUTH = False
else:
    REQUIRE_AUTH = True
print('REQUIRE_AUTH:',REQUIRE_AUTH)

REQUIRE_AUTH: False


## Imports

In [4]:
#| hide
try:
    import nbdev
except:
    print('to convert this notebook to app.py you need to pip install nbdev')

In [41]:
#| export
import os
import gradio as gr
import openai
from pydub import AudioSegment
import io
from datetime import datetime
from math import ceil
from multiprocessing.pool import ThreadPool
from functools import partial
from pathlib import Path
import uuid
from tenacity import (
    retry,
    stop_after_attempt,
    wait_random_exponential,
)  # for exponential backoff
import traceback
# from cartesia.tts import CartesiaTTS
import cartesia
import requests
import urllib
import re

Set the Gradio TEMP directory. This will be used to save audio files that were generated prior to returning them. The reason we are doing this is because if you return a bytesio object to a Gradio audio object it will not contain the file extension and will not be playable in Safari. If you pass the file to the Gradio audio object it will contain the extension. In addition if you pass the filepath instead of bytesio path, when you download the audio it will have the correct file extenion whereas otherwise it will not.

## App Settings/Constants

In [6]:
#| export
TEMP = os.environ.get('GRADIO_TEMP_DIR','/tmp/')
TEMP_DIR = Path(TEMP)
print('TEMP Dir:', TEMP_DIR)

TEMP Dir: /tmp


In [7]:
#| export
#Number of threads created PER USER REQUEST. This throttels the # of API requests PER USER request. This is in ADDITION to the Gradio threads.
OPENAI_CLIENT_TTS_THREADS = 10 
CARTESIAAI_CLIENT_TTS_THREADS = 3

DEFAULT_PROVIDER = 'openai'
DEFAULT_MODEL = 'tts-1'
DEFAULT_VOICE = 'alloy'

In [8]:
#| export
providers = dict()

In [9]:
#| export
# Add OpenAI as a provider
try:
    providers['openai'] = {
        'name': 'Open AI',
        'models': {o.id: o.id for o in openai.models.list().data if 'tts' in o.id},
        'voices': {o:{'id':o,'name':o.title()} for o in ['alloy', 'echo', 'fable', 'onyx', 'nova', 'shimmer']},
        'settings': {'max_chunk_size': 4000, 'chunk_processing_time': 60, 
                     'threads': OPENAI_CLIENT_TTS_THREADS,
                     'audio_file_conversion_kwargs':{'format': 'mp3'}},
    }
    print('Successfully added OpenAI as Provider')
except Exception as e:
    print(f"""Error: Failed to add OpenAI as a provider.\nException: {repr(e)}\nTRACEBACK:\n""",traceback.format_exc())
# providers

Successfully added OpenAI as Provider


In [10]:
#| export
# Add Cartesia AI as a provider
try:
    providers['cartesiaai'] = {
        'name': 'Cartesia AI',
        'models': {'upbeat-moon': 'Sonic Turbo English'},
        'voices': {v['id']:v for k,v in cartesia.tts.CartesiaTTS().get_voices().items()},
        'settings': {'max_chunk_size': 500, 'chunk_processing_time': 20, 
                     'threads': CARTESIAAI_CLIENT_TTS_THREADS,
                     'audio_file_conversion_kwargs':{'format': 'raw', 'frame_rate': 44100, 
                                                     'channels': 1, 'sample_width': 2}},
    }
    print('Successfully added Cartesia AI as Provider')
except Exception as e:
    print(f"""Error: Failed to add Cartesia AI as a provider.\nException: {repr(e)}\nTRACEBACK:\n""",traceback.format_exc())
# providers

Successfully added Cartesia AI as Provider


EXAMPLE: providers
```python
{'openai': {'name': 'Open AI',
  'models': {'tts-1-hd-1106': 'tts-1-hd-1106',
   'tts-1-hd': 'tts-1-hd',
   'tts-1': 'tts-1',
   'tts-1-1106': 'tts-1-1106'},
  'voices': {'alloy': {'id': 'alloy', 'name': 'Alloy'},
   'echo': {'id': 'echo', 'name': 'Echo'},
   'fable': {'id': 'fable', 'name': 'Fable'},
   'onyx': {'id': 'onyx', 'name': 'Onyx'},
   'nova': {'id': 'nova', 'name': 'Nova'},
   'shimmer': {'id': 'shimmer', 'name': 'Shimmer'}}},
 'cartesiaai': {'name': 'Cartesia AI',
  'models': {'upbeat-moon': 'Sonic Turbo English'},
  'voices': {'3b554273-4299-48b9-9aaf-eefd438e3941': {'id': '3b554273-4299-48b9-9aaf-eefd438e3941',
    'user_id': None,
    'is_public': True,
    'name': 'Indian Lady',
    'description': 'This voice is young, rich, and curious, perfect for a narrator or fictional character',
    'created_at': '2024-05-04T18:48:17.006441-07:00',
    'embedding': [0.015546328,-0.11384969,0.14146514, ...]},
   '63ff761f-c1e8-414b-b969-d1833d1c870c': {'id': '63ff761f-c1e8-414b-b969-d1833d1c870c',
    'user_id': None,
    'is_public': True,
    'name': 'Confident British Man',
    'description': 'This voice is disciplined with a British accent, perfect for a commanding character or narrator',
    'created_at': '2024-05-04T18:57:31.399193-07:00',
    'embedding': [-0.056990184,-0.06531749,-0.05618861,...]}
            }
}
```

In [11]:
# {v['id']:v['name'] for k,v in cartesia.tts.CartesiaTTS().get_voices().items()},

```
({'3b554273-4299-48b9-9aaf-eefd438e3941': 'Indian Lady',
  '63ff761f-c1e8-414b-b969-d1833d1c870c': 'Confident British Man',
  'daf747c6-6bc2-4083-bd59-aa94dce23f5d': 'Middle Eastern Woman',
  'ed81fd13-2016-4a49-8fe3-c0d2761695fc': 'Sportsman',
  'f114a467-c40a-4db8-964d-aaba89cd08fa': 'Yogaman',
  'c45bc5ec-dc68-4feb-8829-6e6b2748095d': 'Movieman',
  '87748186-23bb-4158-a1eb-332911b0b708': 'Wizardman',
  '98a34ef2-2140-4c28-9c71-663dc4dd7022': 'Southern Man',
  '79f8b5fb-2cc8-479a-80df-29f7a7cf1a3e': 'Nonfiction Man',
  '36b42fcb-60c5-4bec-b077-cb1a00a92ec6': 'Pilot over Intercom',
  '69267136-1bdc-412f-ad78-0caad210fb40': 'Friendly Reading Man',
  '15a9cd88-84b0-4a8b-95f2-5d583b54c72e': 'Reading Lady',
  '95856005-0332-41b0-935f-352e296aa0df': 'Classy British Man',
  'd46abd1d-2d02-43e8-819f-51fb652c1c61': 'Newsman',
  '2ee87190-8f84-4925-97da-e52547f9462c': 'Child',
  'c2ac25f9-ecc4-4f56-9095-651354df60c0': 'Commercial Lady',
  '5345cf08-6f37-424d-a5d9-8ae1101b9377': 'Maria',
  'a3520a8f-226a-428d-9fcd-b0a4711a6829': 'Reflective Woman',
  'e3827ec5-697a-4b7c-9704-1a23041bbc51': 'Sweet Lady',
  'a0e99841-438c-4a64-b679-ae501e7d6091': 'Barbershop Man',
  'cd17ff2d-5ea4-4695-be8f-42193949b946': 'Meditation Lady',
  'bf991597-6c13-47e4-8411-91ec2de5c466': 'Newslady',
  '41534e16-2966-4c6b-9670-111411def906': "1920's Radioman",
  '79a125e8-cd45-4c13-8a67-188112f4dd22': 'British Lady',
  'a167e0f3-df7e-4d52-a9c3-f949145efdab': 'Ted',
  '248be419-c632-4f23-adf1-5324ed7dbf1d': 'Hannah',
  'c8605446-247c-4d39-acd4-8f4c28aa363c': 'Wise Lady',
  '00a77add-48d5-4ef6-8157-71e5437b282d': 'Calm Lady',
  '638efaaa-4d0c-442e-b701-3fae16aad012': 'Indian Man',
  'd6b6d712-6030-4420-9771-8b35f326fd20': 'Mat 1'},)
```

In [12]:
#| export
CLEAN_TEXT_SYSTEM_PROMPT = """You are a helpful expert AI assistant. You are an autoregressive LLM. Your job is to take markdown that was created from a web page html and clean it up so it can be fed to a text to speech model. Remove all hyperlink URL's, navigation references, citations or complex formulas that are not useful when only listening to in audio format. It is also helpful to spell out dates, long numbers, abbreviations, acronym, units etc. For example if you see `50C` in the context of temperature change it to `50 degrees celsius`. If you see an acronym, for example NASA, please spell it out `National Aeronautics and Space Administration`. When you have finished your task please finish the text you return with <<COMPLETE>>. The maximum context length you can return in one shot is 4,000 tokens so you may get cut off. If that happens I will send you another message with the text <<CONTINUE>> and you should continue the task where you had previously left off. This is why I need you finish your response with <<COMPLETE>> once you have fully completed your task.  DO NOT MODIFY THE TEXT IN ANY WAY EXCEPT FOR AS INSTRUCTED HERE."""


# Main Implementation

In [13]:
#| export
def verify_authorization(profile: gr.OAuthProfile=None) -> str:
    print('Profile:', profile)
    if REQUIRE_AUTH == False:
        return 'WARNING_NO_AUTH_REQUIRED_LOCAL'
    elif profile is not None and profile.username in ALLOWED_OAUTH_PROFILE_USERNAMES:
        return f"{profile.username}"
    else:
        # print('Unauthorized',profile)
        raise PermissionError(f'Your huggingface username ({profile}) is not authorized. Must be set in ALLOWED_OAUTH_PROFILE_USERNAMES environment variable.')
        return None

In [14]:
#| export
def split_text(input_text, provider):
    settings = providers[provider]['settings']
    max_length = settings['max_chunk_size']
    lookback = max_length // 4
        
    # If the text is shorter than the max_length, return it as is
    if len(input_text) <= max_length:
        return [input_text]

    chunks = []
    while input_text:
        # Check if the remaining text is shorter than the max_length
        if len(input_text) <= max_length:
            chunks.append(input_text)
            break

        # Define the split point, initially set to max_length
        split_point = max_length

        # Look for a newline in the last 'lookback' characters
        newline_index = input_text.rfind('\n', max_length-lookback, max_length)
        if newline_index != -1:
            split_point = newline_index + 1  # Include the newline in the current chunk

        # If no newline, look for a period followed by space
        elif '. ' in input_text[max_length-lookback:max_length]:
            # Find the last '. ' in the lookback range
            period_index = input_text.rfind('. ', max_length-lookback, max_length)
            split_point = period_index + 2  # Split after the space

        # Split the text and update the input_text
        chunks.append(input_text[:split_point])
        input_text = input_text[split_point:]

    return chunks

In [15]:
#| export
def concatenate_audio(files:list, **kwargs):

    # Initialize an empty AudioSegment object for concatenation
    combined = AudioSegment.empty()

    # Loop through the list of mp3 binary data
    for data in files:
        # Convert binary data to an audio segment
        audio_segment = AudioSegment.from_file(io.BytesIO(data), **kwargs)
        
        # Concatenate this segment to the combined segment
        combined += audio_segment

    #### Return Bytes Method
    # # Export the combined segment to a new mp3 file
    # # Use a BytesIO object to handle this in memory
    # combined_mp3 = io.BytesIO()
    # combined.export(combined_mp3, format="mp3")

    # # Seek to the start so it's ready for reading
    # combined_mp3.seek(0)

    # return combined_mp3.getvalue()

    #### Return Filepath Method
    filepath = TEMP_DIR/(str(uuid.uuid4())+'.mp3')
    combined.export(filepath, format="mp3")
    print('Saving mp3 file to temp directory: ', filepath)
    return str(filepath)

In [16]:
#| export
def create_speech_openai(chunk_idx, input, model='tts-1', voice='alloy', speed=1.0, **kwargs):
    client = openai.OpenAI()
    
    @retry(wait=wait_random_exponential(min=1, max=180), stop=stop_after_attempt(6))
    def _create_speech_with_backoff(**kwargs):
        return client.audio.speech.create(**kwargs)
    
    response = _create_speech_with_backoff(input=input, model=model, voice=voice, speed=speed, **kwargs)
    client.close()
    return chunk_idx, response.content
if 'openai' in providers.keys():
    providers['openai']['settings']['create_speech_func'] = create_speech_openai
    print('Added create_speech_func for openai provider')

Added create_speech_func for openai provider


```python
client.generate(
    *,
    transcript: str,
    voice: List[float],
    model_id: str = '',
    duration: int = None,
    chunk_time: float = None,
    stream: bool = False,
    websocket: bool = True,
    output_format: Union[str, cartesia._types.AudioOutputFormat] = 'fp32',
    data_rtype: str = 'bytes',
) -> Union[cartesia._types.AudioOutput, Generator[cartesia._types.AudioOutput, NoneType, NoneType]]

list(cartesia._types.AudioOutputFormat)
[<AudioOutputFormat.FP32: 'fp32'>,
 <AudioOutputFormat.PCM: 'pcm'>,
 <AudioOutputFormat.FP32_16000: 'fp32_16000'>,
 <AudioOutputFormat.FP32_22050: 'fp32_22050'>,
 <AudioOutputFormat.FP32_44100: 'fp32_44100'>,
 <AudioOutputFormat.PCM_16000: 'pcm_16000'>,
 <AudioOutputFormat.PCM_22050: 'pcm_22050'>,
 <AudioOutputFormat.PCM_44100: 'pcm_44100'>,
 <AudioOutputFormat.MULAW_8000: 'mulaw_8000'>]
```

In [17]:
#| export
def create_speech_cartesiaai(chunk_idx, input, model='upbeat-moon', 
                             voice='248be419-c632-4f23-adf1-5324ed7dbf1d', #Hannah
                             websocket=False, 
                             output_format='pcm_44100', 
                             **kwargs):
    client = cartesia.tts.CartesiaTTS()
    
    # @retry(wait=wait_random_exponential(min=1, max=180), stop=stop_after_attempt(6))
    def _create_speech_with_backoff(**kwargs):
        return client.generate(**kwargs)
    
    response = _create_speech_with_backoff(transcript=input, model_id=model, 
                                           voice=client.get_voice_embedding(voice_id=voice), 
                                           websocket=websocket, 
                                           output_format=output_format, 
                                           **kwargs)
    client.close()
    return chunk_idx, response["audio"]
if 'cartesiaai' in providers.keys():
    providers['cartesiaai']['settings']['create_speech_func'] = create_speech_cartesiaai
    print('Added create_speech_func for create_speech_cartesiaai provider')

Added create_speech_func for create_speech_cartesiaai provider


In [18]:
# test
# create_speech_cartesiaai(1,"Hi. What's your name?", model='upbeat-moon',
#               voice='63ff761f-c1e8-414b-b969-d1833d1c870c')
# text = """Ladies and Gentlemen, gather 'round your radio sets for a special report on a remarkable phenomenon sweeping the nation! It seems a new generation of prodigies is lighting up our schools and captivating communities from coast to coast. Yes, we're talking about gifted children, those bright young minds whose talents and intellects are far beyond their tender years.
# In classrooms across the country, educators are reporting an unprecedented wave of exceptional youngsters. These gifted children, some as young as five or six, are astonishing their teachers with feats of arithmetic, literacy, and creativity that rival those of much older students. The age of enlightenment is upon us, and it starts with these brilliant boys and girls!
# Take young Tommy Caldwell of Newark, New Jersey, for instance. At the ripe age of seven, Tommy has already mastered algebra and is now diving into the wonders of geometry. His teacher, Miss Grace Whittaker, says she’s never seen such a gifted mathematician in her twenty years of teaching. And Tommy is just one of many!
# Then there's little Sally Henderson of Topeka, Kansas. At the tender age of eight, Sally has penned her first book of poetry, a collection that has local literary circles abuzz with excitement. Her vivid imagination and eloquent verse have earned her the nickname “The Young Bard of Topeka.” The town is swelling with pride for their young poetess.
# Experts from esteemed institutions like Harvard and Yale are paying close attention to this trend, conducting studies to understand the roots of such exceptional abilities. Some suggest it’s the result of improved nutrition and health care, while others believe it’s the progressive educational methods now being employed in our schools. Regardless of the cause, one thing is clear: America is home to a new generation of geniuses!
# Communities are rallying to support these young prodigies, with special programs and schools being established to nurture their extraordinary talents. Parents, teachers, and civic leaders are united in their mission to provide the resources and opportunities these gifted children need to reach their full potential.
# So, dear listeners, as you sit by your radios tonight, take heart in the knowledge that our future is bright. With these remarkable young minds leading the way, the possibilities are endless. This is your announcer signing off, wishing you all a splendid evening and a hopeful tomorrow."""
# _, test_data = create_speech_cartesiaai(1, text, model='upbeat-moon',
#               voice='41534e16-2966-4c6b-9670-111411def906')

In [19]:
# test_file = AudioSegment.from_file(io.BytesIO(test_data), **{'format': 'raw', 'frame_rate': 44100, 'channels': 1, 'sample_width': 2})
# test_file.export('./test3.mp3', format="mp3")

In [20]:
#| export
def create_speech(input_text, provider, model='tts-1', voice='alloy', 
                  profile: gr.OAuthProfile|None=None, # comment out of running locally
                  progress=gr.Progress(), **kwargs):

    #Verify auth if it is required. This is very important if this is in a HF space. DO NOT DELETE!!!
    if REQUIRE_AUTH: verify_authorization(profile)
    start = datetime.now()
    
    settings = providers[provider]['settings']
    create_speech_func = settings['create_speech_func']
    chunk_processing_time = settings['chunk_processing_time']
    threads = settings['threads']
    audio_file_conversion_kwargs = settings['audio_file_conversion_kwargs']
    
    # Split the input text into chunks
    chunks = split_text(input_text, provider=provider)

    # Initialize the progress bar
    progress(0, desc=f"Started processing {len(chunks)} text chunks using {threads} threads. ETA is ~{ceil(len(chunks)/threads)*chunk_processing_time/60.} min.")

    # Initialize a list to hold the audio data of each chunk
    audio_data = []

    # Process each chunk
    with ThreadPool(processes=threads) as pool:
        results = pool.starmap(
            partial(create_speech_func, model=model, voice=voice, **kwargs), 
            zip(range(len(chunks)),chunks)
        )
    audio_data = [o[1] for o in sorted(results)]

    # Progress
    progress(.9, desc=f"Merging audio chunks... {(datetime.now()-start).seconds} seconds to process.")
    
    # Concatenate the audio data from all chunks
    combined_audio = concatenate_audio(audio_data, **audio_file_conversion_kwargs)

    # Final update to the progress bar
    progress(1, desc=f"Processing completed... {(datetime.now()-start).seconds} seconds to process.")
    
    print(f"Processing time: {(datetime.now()-start).seconds} seconds.")

    return combined_audio


In [21]:
# create_speech("Hi. What's your name?", provider='openai', model='tts-1', voice='alloy')
# create_speech("Hi. What's your name?", provider='cartesiaai', model='upbeat-moon',
#               voice='63ff761f-c1e8-414b-b969-d1833d1c870c')

In [22]:
#| export
def get_input_text_len(input_text):
    return len(input_text)

In [23]:
#| export
def get_generation_cost(input_text, tts_model_dropdown, provider):
    text_len = len(input_text)
    if provider == 'openai':
        if tts_model_dropdown.endswith('-hd'):
            cost = text_len/1000 * 0.03
        else:
            cost = text_len/1000 * 0.015
    elif provider == 'cartesiaai':
        cost = text_len/1000 * 0.065
    else:
        raise ValueError(f'Invalid argument provider: {provider}')
    return "${:,.3f}".format(cost)

In [24]:
#| export
def get_model_choices(provider):
    return sorted([(v,k) for k,v in providers[provider]['models'].items()])

In [25]:
#| export
def update_model_choices(provider):
    choices = get_model_choices(provider)
    return gr.update(choices=choices,value=choices[0][1])

In [26]:
#| export
def get_voice_choices(provider, model):
    return sorted([(v['name'],v['id']) for v in providers[provider]['voices'].values()])

In [27]:
#| export
def update_voice_choices(provider, model):
    choices = get_voice_choices(provider, model)
    return gr.update(choices=choices,value=choices[0][1])

In [28]:
#| export
def split_text_as_md(*args, **kwargs):
    output = split_text(*args, **kwargs)
    return '# Text Splits:\n' + '<br>----------<br>'.join(output)

In [42]:
#| export
def remove_urls_from_markdown(text):
    return re.sub(r'\[([^\]]+)\]\([^\)]+\)', r'\1', text)

In [43]:
#| export
def get_page_md(url):
    # result = requests.get('https://r.jina.ai/'+urllib.parse.quote_plus(url))
    result = requests.get('https://r.jina.ai/'+url)
    result.raise_for_status()
    return remove_urls_from_markdown(result.text)

In [47]:
# test_page_md = get_page_md('https://simonwillison.net/2024/Jun/16/jina-ai-reader/')
# test_page_md

In [31]:
#| export
# import json
def clean_page_md(text):
    max_iters = 15
    complete = False
    client = openai.OpenAI()

    tokens = 0
    messages = messages=[
        {"role": "system", "content": CLEAN_TEXT_SYSTEM_PROMPT},
        {"role": "user", "content": text},
        # {"role": "assistant", "content": "The Los Angeles Dodgers won the World Series in 2020."},
        # {"role": "user", "content": "Where was it played?"}
      ]

    idx = 0
    while complete == False and idx < max_iters:
        print('Page Cleaning Iter:',idx)
        assert idx < max_iters
        idx += 1
        response = client.chat.completions.create(
          model="gpt-4o",
          messages=messages
        )
        # print(response,'\n\n\n')
        response_text = response.choices[0].message.content
        if '<<complete>>' in response_text.lower():
            complete = True
        messages += [
            {"role": "assistant", "content": response_text},
            {"role": "user", "content": "Please continue."},
        ]
        tokens += response.usage.total_tokens
        # print(json.dumps(messages, indent=4))

    client.close()
    print('TOKENS CLEANUP:', tokens)
    result = ' '.join([o['content'] for o in messages if o['role'] == 'assistant'])
    
    return result.replace('<<COMPLETE>>','')
# res = clean_page_md(test_page_md)
# res

In [32]:
# clean_page_md(get_page_md('https://www.ineteconomics.org/perspectives/blog/from-long-covid-odds-to-lost-iq-points-ongoing-threats-you-dont-know-about'))

In [48]:
#| export
def get_page_text(url:str, ai_clean:bool):
    text = get_page_md(url)
    if ai_clean:
        text = clean_page_md(text)
    return text

In [50]:
#| export
with gr.Blocks(title='TTS', head='TTS', delete_cache=(3600,3600)) as app:
    
    ### Define UI ###
    gr.Markdown("# TTS")
    gr.Markdown("""Start typing below and then click **Go** to create the speech from your text.
For requests longer than allowed by the API they will be broken into chunks automatically. [Spaces Link](https://matdmiller-tts-openai.hf.space/) | <a href="https://matdmiller-tts-openai.hf.space/" target="_blank">Spaces Link HTML</a>
[https://r.jina.ai/](https://r.jina.ai/)""")
    with gr.Row():
        input_url = gr.Textbox(max_lines=1, label="Optional - Enter a URL")
        input_clean_cb = gr.Checkbox(value=False, label='AI Clean Text')
        get_url_content_btn = gr.Button("Get URL Contents")
    with gr.Row():
        input_text = gr.Textbox(max_lines=100, label="Enter text here")
    with gr.Row():
        tts_provider_dropdown = gr.Dropdown(value=DEFAULT_PROVIDER,
            choices=tuple([(v['name'],k) for k,v in providers.items()]), label='Provider', interactive=True)
        tts_model_dropdown = gr.Dropdown(value=DEFAULT_MODEL,choices=get_model_choices(DEFAULT_PROVIDER), 
                                         label='Model', interactive=True)
        tts_voice_dropdown = gr.Dropdown(value=DEFAULT_VOICE,choices=get_voice_choices(DEFAULT_PROVIDER, DEFAULT_MODEL),
                                         label='Voice', interactive=True)
        input_text_length = gr.Label(label="Number of characters")
        generation_cost = gr.Label(label="Generation cost")
    with gr.Row():
        output_audio = gr.Audio()
    go_btn = gr.Button("Go")
    clear_btn = gr.Button('Clear')
    if REQUIRE_AUTH:
        gr.LoginButton()
        auth_md = gr.Markdown('')
        
    chunks_md = gr.Markdown('',label='Chunks')
    

    ### Define UI Actions ###

    get_url_content_btn.click(fn=get_page_text, inputs=[input_url,input_clean_cb], outputs=input_text)
    
    # input_text 
    input_text.input(fn=get_input_text_len, inputs=input_text, outputs=input_text_length)
    input_text.input(fn=get_generation_cost, 
                     inputs=[input_text,tts_model_dropdown,tts_provider_dropdown], 
                     outputs=generation_cost)
    input_text.input(fn=split_text_as_md, inputs=[input_text,tts_provider_dropdown], outputs=chunks_md)
    
    # tts_provider_dropdown
    tts_provider_dropdown.change(fn=update_model_choices, inputs=[tts_provider_dropdown], 
                                 outputs=tts_model_dropdown)
    tts_provider_dropdown.change(fn=update_voice_choices, inputs=[tts_provider_dropdown, tts_model_dropdown], 
                                 outputs=tts_voice_dropdown)
    tts_provider_dropdown.change(fn=split_text_as_md, inputs=[input_text,tts_provider_dropdown], outputs=chunks_md)
    
    # tts_model_dropdown
    tts_model_dropdown.change(fn=get_generation_cost, 
                              inputs=[input_text,tts_model_dropdown,tts_provider_dropdown], outputs=generation_cost)
    
    
    go_btn.click(fn=create_speech, 
                 inputs=[input_text, tts_provider_dropdown, tts_model_dropdown, tts_voice_dropdown], 
                 outputs=[output_audio])
    
    
    clear_btn.click(fn=lambda: '', outputs=input_text)

    if REQUIRE_AUTH:
        app.load(verify_authorization, None, auth_md)
    
    

In [51]:
#| export
# launch_kwargs = {'auth':('username',GRADIO_PASSWORD),
#                  'auth_message':'Please log in to Mat\'s TTS App with username: username and password.'}
launch_kwargs = {}
queue_kwargs = {'default_concurrency_limit':10}

In [52]:
#| hide
#Notebook launch
app.queue(**queue_kwargs)
app.launch(**launch_kwargs)

Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


In [ ]:
#| export
#.py launch
if __name__ == "__main__":
    app.queue(**queue_kwargs)
    app.launch(**launch_kwargs)

In [45]:
#| hide
app.close()

Closing server running on port: 7860


In [ ]:
#| hide
gr.close_all()

In [53]:
#| hide
import nbdev
nbdev.export.nb_export('app.ipynb',lib_path='.')